In [1]:
from pyomo.environ import *
from pyomo.opt import *
opt = solvers.SolverFactory("glpk")

In [2]:
T = {'Start':0,
     'A':2,
     'B':4,
     'C':10,
     'D':6,
     'E':4,
     'F':5,
     'G':7,
     'H':9,
     'I':7,
     'J':8,
     'K':4,
     'L':5,
     'M':2,
     'N':6,
     'Finish':0}

R = {'Start':0,
     'A':1,
     'B':2,
     'C':3,
     'D':2,
     'E':1,
     'F':2,
     'G':3,
     'H':3,
     'I':2,
     'J':2,
     'K':1,
     'L':2,
     'M':1,
     'N':3,
     'Finish':0}

C = {'Start':0,
     'A':100,
     'B':50,
     'C':80,
     'D':40,
     'E':160,
     'F':40,
     'G':40,
     'H':60,
     'I':30,
     'J':30,
     'K':40,
     'L':50,
     'M':100,
     'N':60,
     'Finish':0}

In [3]:
P = {'Start':[],
     'A':['Start'],
     'B':['A'],
     'C':['B'],
     'D':['C'],
     'E':['C'],
     'F':['E'],
     'G':['D'],
     'H':['G','E'],
     'I':['C'],
     'J':['F','I'],
     'K':['J'],
     'L':['J'],
     'M':['H'],
     'N':['K','L'],
     'Finish':['M','N']}

N = list(T.keys())
A = [(j,i) for i in N for j in P[i]]

In [4]:
model = ConcreteModel()
model.t = Var(N, within=NonNegativeReals)
model.x = Var(N, within=NonNegativeReals)

In [5]:
def time_rule(model, i, j):
    return model.t[j] >= model.t[i] + T[i] - model.x[i]
    
model.time = Constraint(A, rule=time_rule)

model.start = Constraint(expr = model.t['Start'] == 0)
model.finish = Constraint(expr = model.t['Finish'] <= 28)

def crash_rule(model, n):
    return model.x[n] <= R[n]

model.crash = Constraint(N, rule=crash_rule)

model.cost = Objective(expr = sum(model.x[n]*C[n] for n in N), sense=minimize)

In [6]:
model.dual = Suffix(direction=Suffix.IMPORT)
results = opt.solve(model)
model.x.get_values()

{'A': 1.0,
 'B': 2.0,
 'C': 3.0,
 'D': 2.0,
 'E': 1.0,
 'F': 2.0,
 'Finish': 0.0,
 'G': 3.0,
 'H': 1.0,
 'I': 1.0,
 'J': 2.0,
 'K': 1.0,
 'L': 2.0,
 'M': 0.0,
 'N': 3.0,
 'Start': 0.0}

In [7]:
model.t.get_values()

{'A': 0.0,
 'B': 1.0,
 'C': 3.0,
 'D': 10.0,
 'E': 10.0,
 'F': 13.0,
 'Finish': 28.0,
 'G': 14.0,
 'H': 18.0,
 'I': 10.0,
 'J': 16.0,
 'K': 22.0,
 'L': 22.0,
 'M': 26.0,
 'N': 25.0,
 'Start': 0.0}

In [8]:
model.cost.expr()

1350.0

In [9]:
for (i,j) in A:
    print ((i,j), model.dual[model.time[(i,j)]])

('Start', 'A') 0.0
('A', 'B') -250.0
('B', 'C') -250.0
('C', 'D') -60.0
('C', 'E') -160.0
('E', 'F') -160.0
('D', 'G') -60.0
('G', 'H') -60.0
('E', 'H') 0.0
('C', 'I') -30.0
('F', 'J') -160.0
('I', 'J') -30.0
('J', 'K') -140.0
('J', 'L') -50.0
('H', 'M') -60.0
('K', 'N') -140.0
('L', 'N') -50.0
('M', 'Finish') -60.0
('N', 'Finish') -190.0


In [10]:
for n in N:
    print(n, model.dual[model.crash[n]])

Start 0.0
A -150.0
B -200.0
C -170.0
D -20.0
E 0.0
F -120.0
G -20.0
H 0.0
I 0.0
J -160.0
K -100.0
L 0.0
M 0.0
N -130.0
Finish 0.0
